In [6]:
import os
import shutil 
import librosa
import pandas as pd
# from IPython.display import clear_output
import numpy as np
# import matplotlib.pyplot as plt
# import tensorflow as tf
import soundfile as sf
# from moviepy.audio.io.AudioFileClip import AudioFileClip
from sklearn.preprocessing import StandardScaler

In [7]:
annotations__path = "IsoDataset/Ann/Chordlab"
lab_path = "IsoDatasetPro/Chordlab"
m4a_song_path = "IsoDataset/Songs/"
wav_song_path = "IsoDatasetPro/Songs/"
IsoDataset = "IsoDataset/"
IsoDatasetPro = "IsoDatasetPro/"
standardized_file = "IsoDatasetPro/Standardized"
chord_vocab_file = "IsoDatasetPro/chord_vocabulary_12_keys.csv"
combined_fpath = "IsoDatasetPro/CombinedData"


In [ ]:
# cOPIES the lab files from the IsoDataset/Ann/Chordlab directory to the IsoDatasetPro/Chordlab directory

available_annotations = []
# Loop through subdirectories in the Ann directory
for subdir in os.listdir(annotations__path):
    subdir_path = os.path.join(annotations__path, subdir)
    
    if os.path.isdir(subdir_path):  # Check if it's a directory
        # Create corresponding output subdirectory if it doesn't exist
        output_subdir = os.path.join(lab_path)
        os.makedirs(output_subdir, exist_ok=True)
        
        # Loop through files in the subdirectory
        for file in os.listdir(subdir_path):
            if file.endswith('.lab'):  # Check if the file is .lab
                input_lab_file = os.path.join(subdir_path, file)
                output_lab_file = os.path.join(output_subdir, f"{subdir}_{file[:2]}.lab")  # Corrected this line
                available_annotations.append(f"{subdir}_{file[:2]}")
                # Copy the .lab file to the new location
                shutil.copy(input_lab_file, output_lab_file)
                print(f"Copied {input_lab_file} to {output_lab_file}")

print(available_annotations)



In [3]:
# cONVERTS THE .m4a FILES TO .wav FILES


def convert_m4a_to_wav(m4a_song_path, wav_song_path):
    # Load the .m4a file using AudioFileClip
    audio_clip = AudioFileClip(m4a_song_path)
    
    # Write to .wav format
    audio_clip.write_audiofile(wav_song_path)

# Loop through subdirectories
for subdir in os.listdir(m4a_song_path):
    subdir_path = os.path.join(m4a_song_path, subdir)
    
    if os.path.isdir(subdir_path) :  # Check if it's a directory
        # Create corresponding output subdirectory if it doesn't exist
        output_subdir = os.path.join(wav_song_path)
        os.makedirs(output_subdir, exist_ok=True)
    
        # Loop through files in the subdirectory
        for file in os.listdir(subdir_path):
            if file.endswith('.m4a'):  # Check if the file is .m4a
                input_file = os.path.join(subdir_path, file)
                newfile = f"0{subdir}_{file.replace('.m4a', '')[:2]}.wav"
                output_file = os.path.join(output_subdir, newfile)

                # Convert and save the .m4a to .wav
                if newfile.removesuffix('.wav') in available_annotations:
                    convert_m4a_to_wav(input_file, output_file)
                    print(f"Converted {input_file} to {output_file}")
                else:
                    print(f"Skipping {input_file} as corresponding annotation not found")


FileNotFoundError: [WinError 3] The system cannot find the path specified: 'IsoDataset/Songs/'

In [ ]:
# Function to extract chroma features from an audio file
# Returns a tuple of the chroma features and the sample rate

#STFT
def extract_chroma_features(audio_file_path, sr=22050, hop_length=512):
    # Load the audio file
    y, sr = librosa.load(audio_file_path, sr=sr)
    
    # Extract chroma features (12 bins per octave)
    chroma = librosa.feature.chroma_stft(y=y, sr=sr, hop_length=hop_length)
    
    # Optionally, normalize the chroma features
    chroma = librosa.util.normalize(chroma)
    
    return chroma, sr


# #CQT
# def extract_features(audio_file_path):
#     y, sr = librosa.load(audio_file_path, sr=22050)
#     cqt = librosa.cqt(y, sr=sr, hop_length=2048, bins_per_octave=24, n_bins=192)  # CQT representation
#     time_steps = librosa.times_like(cqt[0], sr=sr)  # Get time axis for spectrogram
#     cqt = np.abs(cqt) # Get the absolute amplitude (magnitude) of the CQT
#     time_steps = librosa.times_like(cqt[0], sr=sr)  # Get time axis for spectrogram
#     return cqt, time_steps

# def extract_features(audio_file_path):
#     y, sr = librosa.load(audio_file_path, sr=22050)
#     cqt = librosa.cqt(y, sr=sr, hop_length=2048, bins_per_octave=24, n_bins=192)  # CQT representation
#     cqt = np.abs(cqt)  # Get magnitude
#     # Apply Log Scaling
#     cqt = np.log1p(cqt)
#     cqt = librosa.util.normalize(cqt)
#     time_steps = librosa.times_like(cqt[0], sr=sr)  # Get time axis for spectrogram
    
#     return cqt, time_steps

In [ ]:
# Loop through all the .wav files in the subdirectory
for audio_file in os.listdir(wav_song_path):
    audio_file_path = os.path.join(wav_song_path, audio_file)
    print(f"Processing {audio_file_path}")
    # List all .wav files in the subdirectory
    audio_files = [f for f in wav_song_path if f.endswith('.wav')]

    # Extract chroma features
    chroma, sr = extract_chroma_features(audio_file_path)

    # Plotting the chroma features
    plt.figure(figsize=(10, 6))
    librosa.display.specshow(chroma, x_axis='time', y_axis='chroma', sr=sr)
    plt.colorbar(label='Chroma Magnitude')
    plt.title(f'Chroma Feature Plot: {audio_file}')
    plt.show()
    clear_output(wait=True)


In [ ]:

# Function to load .lab file
def load_lab_file(lab_path):
    df = pd.read_csv(lab_path, sep='\s+', header=None, names=["start", "end", "chord"])
    return df

# Function to align labels
def align_labels(time_steps, annotations):
    labels = []
    for t in time_steps:
        chord = "N"  # Default to 'N' (No chord)
        for _, row in annotations.iterrows():
            if row["start"] <= t < row["end"]:
                chord = row["chord"]
                break
        labels.append(chord)
    return np.array(labels)


In [ ]:
# CONVERTING CHORDS TO CHROMA FEATURES

chroma_data = {}  # Store chroma features with file names as keys

# Loop through Songs
if os.path.isdir(wav_song_path):  # Ensure it's a directory
    for file in os.listdir(wav_song_path):
        if file.endswith('.wav'):
            print(f"Extracting chroma for {file}...")
            audio_file_path = os.path.join(wav_song_path, file)
            chroma, time_steps = extract_features(audio_file_path)  # Extract chroma

            chroma_data[file.replace('.wav', '')] = (chroma, time_steps)  # Store without extension
            print(chroma)
            print(f"Extracted chroma for {file}, shape: {chroma.shape}")
print(chroma_data)


In [ ]:
# LOAD CHORD LABELS

chord_labels_data = {}  # Store chord labels with file names as keys

# Loop through Chordlab
if os.path.isdir(lab_path):  # Ensure it's a directory
    for file in os.listdir(lab_path):
        if file.endswith('.lab'):
            lab_file_path = os.path.join(lab_path, file)
            annotations = load_lab_file(lab_file_path)  # Load chord labels

            chord_labels_data[file.replace('.lab', '')] = annotations  # Store without extension

            print(f"Loaded chord labels for {file}")
print(chord_labels_data)


In [ ]:
# COMBINE CHROMA AND CHORD LABELS

combined_data = {}  # Store combined data
print(chroma_data.keys())
for key in chroma_data.keys():
    if key in chord_labels_data:  # Check if matching lab file exists
        print(key)
        chroma, time_steps = chroma_data[key]
        annotations = chord_labels_data[key]

        hop_length = 2048
        timestamps = np.arange(chroma.T.shape[0]) * hop_length / 22050
        timestamps = np.round(timestamps, 4)

        chord_labels = align_labels(timestamps, annotations)  # Align chord labels

        combined_data[key] = (chroma, chord_labels)  # Store final processed data

        print(f"Combined data for {key}: Chroma shape: {chroma.shape}, Chords: {chord_labels[:10]}")

       # Define the directory to save CSV files
        csv_save_dir = "IsoDatasetPro/CombinedData"
        os.makedirs(csv_save_dir, exist_ok=True)

        for key, (chroma, chord_labels) in combined_data.items():
            # Transpose chroma so that time steps are rows
            chroma = chroma.T  # Now shape (N, 192), matching chord_labels (N,)

            # Convert to DataFrame
            df = pd.DataFrame(chroma, columns=[f"CQT_{i}" for i in range(192)])

            # Add chord labels
            df["Chord_Label"] = chord_labels

        # Save to CSV
        save_path = os.path.join(csv_save_dir, f"{key}.csv")
        df.to_csv(save_path, index=False)

        print(f"Saved combined data for {key} at {save_path}")


    else:
        print(f"Warning: No chord labels found for {key}")


In [5]:
# Define categories (merging 'X' into 'N')
roots = ['C', 'C#', 'D', 'D#', 'E', 'F', 'F#', 'G', 'G#', 'A', 'A#', 'B', 'N', 'X']
basses = ['C', 'C#', 'D', 'D#', 'E', 'F', 'F#', 'G', 'G#', 'A', 'A#', 'B', 'N', 'X']
triads = ['Major', 'Minor', 'Diminished', 'Augmented', 'Sus2', 'Sus4', 'N', 'X']
fourths = ['dim7', 'min7', 'maj7', 'maj6', 'N', 'X']

# Mapping flats to sharps (for example 'Db' -> 'C#', 'Eb' -> 'D#', etc.)
flat_to_sharp_mapping = {
    'Db': 'C#', 'Eb': 'D#', 'Fb': 'E', 'Gb': 'F#', 'Ab': 'G#', 'Bb': 'A#', 'Cb': 'B', 'Fb': 'E', 'B#': 'C', 'E#': 'F'
}

In [ ]:
# STANDARD CHORDS

standard_chords_file = "IsoDatasetPro/standard_chords.csv"
os.makedirs(standardized_file, exist_ok=True)

# Load the standard chords mapping
standard_df = pd.read_csv(standard_chords_file)
chord_mapping = dict(zip(standard_df['chord'], standard_df['standardized_label']))

# Function to replace flats with sharps in chord names
def replace_flats_in_chord(chord):
    for flat, sharp in flat_to_sharp_mapping.items():
        chord = chord.replace(flat, sharp)
    return chord

# Loop through each sample file in the directory
for file in os.listdir(combined_fpath):
    if file.endswith(".csv"):  # Ensure only CSV files are processed
        print(f"Processing sample: {file}")
        
        combined_file = os.path.join(combined_fpath, file)
        
        if os.path.exists(combined_file):
            df = pd.read_csv(combined_file)

            print("Before standard replacement:")
            print(df['Chord_Label'].unique())

            # Replace incorrect labels with correct ones
            df.replace({'Chord_Label': chord_mapping}, inplace=True)

            print("After standard replacement:")
            print(df['Chord_Label'].unique())

            # Now apply flat to sharp replacement for each chord label
            df['Chord_Label'] = df['Chord_Label'].apply(replace_flats_in_chord)

            print("After replacing flats with sharps:")
            print(df['Chord_Label'].unique())
            
            # Save the corrected file
            save_path = os.path.join(standardized_file, file)
            df.to_csv(save_path, index=False)
            print(f"Updated: {file}")

print("Processing complete!")


In [8]:
# Dataset Expansion
exp_song_path = "IsoDatasetPro/Expanded/Songs"
exp_file_path = "IsoDatasetPro/Expanded/Files"

scale = ['C', 'C#', 'D', 'D#', 'E', 'F', 'F#', 'G', 'G#', 'A', 'A#', 'B']


In [9]:
def extract_features(audio_file_path):
    # Load audio file
    y, sr = librosa.load(audio_file_path, sr=22050, mono=True)

    # Compute CQT representation
    cqt = librosa.cqt(y, sr=sr, hop_length=2048, bins_per_octave=24, n_bins=192)
    cqt = np.abs(cqt)  # Take the magnitude (absolute value)
    time_steps = librosa.times_like(cqt[0], sr=sr)  # Get time axis for spectrogram

    # Define octave weights (you can customize these)
    octave_weights = np.array([1, 1.2, 1.5, 1.8, 2, 2.5, 3, 4])  # Weights for 8 octaves

    # Initialize weights as an array of ones
    weights = np.ones(cqt.shape)

    # Iterate over each time step (column in CQT)
    for t in range(cqt.shape[1]):
        # Get the top 4 most prominent frequency bins for this time step
        top_4_indices = np.argsort(cqt[:, t])[-4:]  # Indices of top 4 bins

        # Determine which octaves these frequencies belong to
        for idx in top_4_indices:
            octave = idx // 24  # Find the octave of this bin
            weights[idx, t] = octave_weights[octave]  # Apply the octave's weight


    # Apply the weights to the CQT
    cqt_weighted = cqt * weights

    return cqt_weighted, time_steps

In [10]:
# DATA AUGMENTATION

# Function to shift pitch of an audio file
def pitch_shift_audio(audio_file_path, shift_steps):
    for file in os.listdir(audio_file_path):
        if file.endswith('.wav'):
            file_path = os.path.join(audio_file_path, file)
            file_name = file.split('.')[0]
            # Load the audio file
            y, sr = librosa.load(file_path, sr=22050, mono=True)

            # Generate Gaussian noise
            noise_level = 0.01  # Adjust noise level as needed
            gaussian_noise = np.random.normal(0, noise_level, y.shape)

            # Add noise to the audio signal
            y_noisy = y + gaussian_noise

            # Save the noisy audio

            for i in range(-shift_steps, shift_steps + 1):
                # Pitch shift by i semitones
                y_shifted = librosa.effects.pitch_shift(y=y_noisy, sr=sr, n_steps=i)

                # Save the shifted audio to a new file
                save_path = os.path.join(exp_song_path, f"{file_name}_({i}).wav")
                sf.write(save_path, y_shifted, sr)
                print(f"Saved {save_path}")

# Function to shift pitch of chord labels
def shift_chord(chord, semitone_shift):
    if (chord == 'N' or chord == 'X'or semitone_shift == 0):
        return chord
    else:
        root = chord.split(':')[0]  # Extract root note (like 'C', 'G', 'D#')
        quality = chord.split(':')[1] 

        # Find the current index of the root note
        root_idx = scale.index(root)

        # Shift the root note by `i` semitones
        new_root = scale[(root_idx + semitone_shift) % 12]

        # Return the shifted chord
        # print(f'{root}:{quality} -> {new_root}:{quality}')
        return f'{new_root}:{quality}'

# Function to shift pitch of chord labels in CSV files
def pitch_shift_files(csv_file_path, song_path, shift_steps):
    print(csv_file_path)
    for file in os.listdir(csv_file_path):
        print(f"Processing {file}")
        if file.endswith('.csv'):
            file_path = os.path.join(csv_file_path, file)
            file_name = file.split('.')[0]

            for i in range(-shift_steps, shift_steps + 1):
                df = pd.read_csv(file_path)
                # Shift the chord labels by i semitones
                df['Chord_Label'] = df['Chord_Label'].apply(lambda x: shift_chord(x, i))
                new_file = f"{file_name}_({i}).csv"
                print(f"Processing:{new_file}")
                
                song = song_path + '/' + new_file.replace('.csv', '.wav')
                print(f"Processing:{song}")
                chroma, sr = extract_features(song)
                print(chroma)

                # Calculate timestamp for each frame (hop_length = 512)
                hop_length = 2048
                timestamps = np.arange(chroma.T.shape[0]) * hop_length / 22050
                timestamps = np.round(timestamps, 4)

                # Replace the first 12 columns with new chroma data
                newdf = pd.DataFrame(chroma.T, columns=[f"CQT_{i}" for i in range(192)])
                newdf["Chord_Label"] = df["Chord_Label"]
                newdf["Timestamp"] = timestamps
                df = newdf
                print(df)

                # Save the shifted data to a new file
                save_path = os.path.join(exp_file_path, f"{file_name}_({i}).csv")
                df.to_csv(save_path, index=False)
                print(f"Saved {save_path}\n")


In [9]:
pitch_shift_audio(wav_song_path, 5)


Saved IsoDatasetPro/Expanded/Songs\01_01_(-5).wav
Saved IsoDatasetPro/Expanded/Songs\01_01_(-4).wav
Saved IsoDatasetPro/Expanded/Songs\01_01_(-3).wav
Saved IsoDatasetPro/Expanded/Songs\01_01_(-2).wav
Saved IsoDatasetPro/Expanded/Songs\01_01_(-1).wav
Saved IsoDatasetPro/Expanded/Songs\01_01_(0).wav
Saved IsoDatasetPro/Expanded/Songs\01_01_(1).wav
Saved IsoDatasetPro/Expanded/Songs\01_01_(2).wav
Saved IsoDatasetPro/Expanded/Songs\01_01_(3).wav
Saved IsoDatasetPro/Expanded/Songs\01_01_(4).wav
Saved IsoDatasetPro/Expanded/Songs\01_01_(5).wav
Saved IsoDatasetPro/Expanded/Songs\01_02_(-5).wav
Saved IsoDatasetPro/Expanded/Songs\01_02_(-4).wav
Saved IsoDatasetPro/Expanded/Songs\01_02_(-3).wav
Saved IsoDatasetPro/Expanded/Songs\01_02_(-2).wav
Saved IsoDatasetPro/Expanded/Songs\01_02_(-1).wav
Saved IsoDatasetPro/Expanded/Songs\01_02_(0).wav
Saved IsoDatasetPro/Expanded/Songs\01_02_(1).wav
Saved IsoDatasetPro/Expanded/Songs\01_02_(2).wav
Saved IsoDatasetPro/Expanded/Songs\01_02_(3).wav
Saved IsoD

In [12]:
pitch_shift_files(standardized_file, exp_song_path, 5)
print("Processing complete!")

IsoDatasetPro/Standardized
Processing 01_01.csv
Processing:01_01_(-5).csv
Processing:IsoDatasetPro/Expanded/Songs/01_01_(-5).wav
[[0.01373213 0.0146917  0.01284157 ... 0.01439316 0.0117499  0.00812288]
 [0.01037383 0.0108295  0.00965391 ... 0.01225162 0.00889069 0.00496181]
 [0.00850648 0.01092241 0.01175883 ... 0.01107952 0.00877356 0.00555354]
 ...
 [0.00529707 0.00345794 0.0076046  ... 0.00485627 0.00351147 0.00255042]
 [0.00484373 0.00209563 0.0085126  ... 0.00502914 0.00223122 0.00245228]
 [0.00290233 0.00186155 0.00244976 ... 0.00250298 0.00092901 0.00056616]]
         CQT_0     CQT_1     CQT_2     CQT_3     CQT_4     CQT_5     CQT_6  \
0     0.013732  0.010374  0.008506  0.006940  0.005783  0.004864  0.001814   
1     0.014692  0.010829  0.010922  0.008918  0.006181  0.005791  0.003469   
2     0.012842  0.009654  0.011759  0.010276  0.004662  0.006137  0.005742   
3     0.008362  0.007820  0.010201  0.011168  0.001596  0.006045  0.006914   
4     0.003485  0.006039  0.007543  0

In [ ]:
exp_file_path = "IsoDatasetPro/Expanded/Files"
csv_file_path = "IsoDatasetPro/Expanded/Files"
# Function to convert existing CSV files to Parquet
def convert_csv_to_parquet(csv_file_path, exp_file_path):
    print(csv_file_path)
    for file in os.listdir(csv_file_path):
        if file.endswith('.csv'):
            file_path = os.path.join(csv_file_path, file)
            file_name = file.split('.')[0]

            # Read the CSV file into a DataFrame
            df = pd.read_csv(file_path)

            # Save the DataFrame as Parquet
            save_path = os.path.join(exp_file_path, f"{file_name}.parquet")
            df.to_parquet(save_path, engine="pyarrow", compression="gzip")
            print(f"Converted {file} to {save_path}\n")

            os.remove(file_path)
            print(f"Deleted original CSV file: {file_path}\n")

convert_csv_to_parquet(csv_file_path, exp_file_path)

In [ ]:
file = 'IsoDatasetPro/Expanded/Files/09_11_(3).parquet'
pfile = 'IsoDatasetPro/Expanded/09_11_(3).parquet'
cfile = 'IsoDatasetPro/Expanded/09_11_(3).csv'

df = pd.read_csv(cfile)
# df = df.iloc[:, 0:]
# df.head()

# df.to_csv(cfile)

# df = pd.read_csv(cfile)

df.to_parquet(file)

# df = pd.read_parquet(pfile)
# print(df)
# df.to_csv(cfile)

